In [1]:
import numpy as np
import pandas as pd
import math
from geopy.geocoders import Nominatim
import time

In [2]:
df=pd.read_csv("Crime_Street_Filled.csv")
df

INCIDENT_NUMBER  OFFENSE_CODE            OFFENSE_CODE_GROUP DISTRICT  \
0           I182070945           619                       Larceny      D14   
1           I182070885           619                       Larceny       B3   
2           I182070816           619                       Larceny       C6   
3           I182070777           619                       Larceny      C11   
4           I182070707           619                       Larceny      D14   
...                ...           ...                           ...      ...   
313430   I130126035-00           338                       Robbery      C11   
313431   I130041200-00           547  Burglary - No Property Taken       B3   
313432   I120720047-00           334                       Robbery      E13   
313433   I120719309-00           530           Commercial Burglary       A1   
313434   I060168073-00          1864                Drug Violation      E13   

        REPORTING_AREA  OCCURRED_ON_DATE        Lat       Long  \
0                808.0  02-09-2018 13:00  42.357791 -71.139371   
1                456.0  03-09-2018 17:17  42.301546 -71.081182   
2                185.0  03-09-2018 12:45  42.321987 -71.062807   
3                388.0  23-08-2018 13:34  42.272306 -71.067214   
4                782.0  02-09-2018 23:12  42.352935 -71.140501   
...                ...               ...        ...        ...   
313430           252.0  09-02-2016 13:55        NaN        NaN   
313431           428.0  07-12-2015 11:38  42.314334 -71.097914   
313432           565.0  17-07-2015 09:23        NaN        NaN   
313433           119.0  27-07-2015 12:00  42.352418 -71.065255   
313434           912.0  27-01-2018 14:01  42.322838 -71.100967   

                                               NAME             STREET  \
0                         LARCENY OTHER $200 & OVER         LINCOLN ST   
1                         LARCENY OTHER $200 & OVER       ELLINGTON ST   
2                         LARCENY OTHER $200 & OVER  MASSACHUSETTS AVE   
3                         LARCENY OTHER $200 & OVER           ADAMS ST   
4                         LARCENY OTHER $200 & OVER          GORDON ST   
...                                             ...                ...   
313430                ROBBERY - UNARMED - RESIDENCE     SAVIN HILL AVE   
313431        B&E NON-RESIDENCE DAY - NO PROP TAKEN         DIXWELL ST   
313432                 ROBBERY - UNARMED - BUSINESS                NaN   
313433              B&E NON-RESIDENCE NIGHT - FORCE        BOYLSTON ST   
313434  DRUGS - POSS CLASS D - INTENT MFR DIST DISP          CENTRE ST   

                           LAT_LONG              LAT_LONG_6F  \
0       (42.35779134, -71.13937053)   (42.357791, -71.13937)   
1       (42.30154555, -71.08118184)  (42.301545, -71.081181)   
2       (42.32198656, -71.06280666)  (42.321986, -71.062806)   
3       (42.27230624, -71.06721386)  (42.272306, -71.067213)   
4       (42.35293536, -71.14050052)    (42.352935, -71.1405)   
...                             ...                      ...   
313430                          NaN                      NaN   
313431  (42.31433402, -71.09791405)  (42.314334, -71.097914)   
313432                          NaN                      NaN   
313433  (42.35241815, -71.06525499)  (42.352418, -71.065254)   
313434  (42.32283759, -71.10096723)  (42.322837, -71.100967)   

                LAT_LONG_4F   Lat_4f  Long_4f  
0       (42.3577, -71.1393)  42.3577 -71.1393  
1       (42.3015, -71.0811)  42.3015 -71.0811  
2       (42.3219, -71.0628)  42.3219 -71.0628  
3       (42.2723, -71.0672)  42.2723 -71.0672  
4       (42.3529, -71.1405)  42.3529 -71.1405  
...                     ...      ...      ...  
313430                  NaN      NaN      NaN  
313431  (42.3143, -71.0979)  42.3143 -71.0979  
313432                  NaN      NaN      NaN  
313433  (42.3524, -71.0652)  42.3524 -71.0652  
313434  (42.3228, -71.1009)  42.3228 -71.1009  

[313435 rows x 15 columns]

In [3]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT               1538
REPORTING_AREA        19433
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F           19915
Lat_4f                19915
Long_4f               19915
dtype: int64

In [4]:
df.nunique()

INCIDENT_NUMBER       278714
OFFENSE_CODE             217
OFFENSE_CODE_GROUP        67
DISTRICT                  12
REPORTING_AREA           878
OCCURRED_ON_DATE      229509
Lat                    18115
Long                   18115
NAME                     217
STREET                  3879
LAT_LONG               18130
LAT_LONG_6F            18126
LAT_LONG_4F            17807
Lat_4f                  1567
Long_4f                 1677
dtype: int64

# FUZZY CLEANING STREET COLUMN

In [5]:
import pandas as pd
import re
from rapidfuzz import fuzz, process

def fuzzy_clean_street(df, col="STREET", threshold=85):
    """
    Performs fuzzy deduplication on a street column.
    
    Args:
        df (pd.DataFrame): Input DataFrame
        col (str): Column name to clean
        threshold (int): Similarity score threshold for grouping

    Returns:
        pd.DataFrame: Original DataFrame with extra columns:
                      - <col>_NORM: normalized street
                      - <col>_CLEAN: canonical/fuzzy-cleaned street
    """
    
    # 1️⃣ Normalize street names safely
    def normalize_street(s):
        if pd.isna(s):
            return None
        s = str(s).upper()
        s = re.sub(r'[^A-Z ]', '', s)  # remove numbers/symbols
        s = re.sub(r'\s+', ' ', s)     # remove extra spaces
        return s.strip()
    
    norm_col = f"{col}_NORM"
    clean_col = f"{col}_CLEAN"
    
    df[norm_col] = df[col].apply(normalize_street)
    
    # 2️⃣ Fuzzy grouping (ignore nulls)
    groups = {}
    for street in df[norm_col].dropna():
        match, score, _ = process.extractOne(
            street, groups.keys(), scorer=fuzz.token_sort_ratio
        ) if groups else (None, 0, None)
        
        if score >= threshold:
            groups[match].append(street)
        else:
            groups[street] = [street]
    
    # 3️⃣ Create canonical mapping
    canonical_map = {}
    for k, v in groups.items():
        for item in v:
            canonical_map[item] = k
    
    df[clean_col] = df[norm_col].map(canonical_map)
    
    return df


In [6]:
df = fuzzy_clean_street(df, col="STREET", threshold=85)

In [7]:
df.nunique()

INCIDENT_NUMBER       278714
OFFENSE_CODE             217
OFFENSE_CODE_GROUP        67
DISTRICT                  12
REPORTING_AREA           878
OCCURRED_ON_DATE      229509
Lat                    18115
Long                   18115
NAME                     217
STREET                  3879
LAT_LONG               18130
LAT_LONG_6F            18126
LAT_LONG_4F            17807
Lat_4f                  1567
Long_4f                 1677
STREET_NORM             3877
STREET_CLEAN            3825
dtype: int64

In [8]:
df['STREET_CLEAN'] = df['STREET_CLEAN'].astype(str).str.strip()
df['STREET_CLEAN'].replace(['', ' '], np.nan, inplace=True)

In [9]:
df['STREET_CLEAN'] = df['STREET_CLEAN'].replace('nan', np.nan)

In [10]:
street_to_coords = (
    df.dropna(subset=['STREET_CLEAN', 'LAT_LONG_4F'])
      .groupby('STREET_CLEAN')['LAT_LONG_4F']
      .apply(list)
      .to_dict()
)


In [11]:
mask = df['LAT_LONG_4F'].isna()

df.loc[mask, 'LAT_LONG_4F'] = (
    df.loc[mask, 'STREET_CLEAN']
      .map(lambda s: np.random.choice(street_to_coords.get(s, [np.nan])))
)

In [12]:
df.isnull().sum()
# LAT_LONG_4F           19278

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT               1538
REPORTING_AREA        19433
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN           8658
dtype: int64

# FILLING REPORTING_AREA COLUMN

In [13]:
# {i:df[(df["STREET"]==i)]["REPORTING_AREA"].unique().tolist() for i in df["STREET"].unique()}


street_to_area = (
    df.dropna(subset=['STREET_CLEAN', 'REPORTING_AREA'])
    .groupby(['STREET_CLEAN'])['REPORTING_AREA']
    .agg(lambda x: x.value_counts().idxmax())
    .to_dict()
)

street_to_area

{'A ST': 205.0,
 'ABBOT ST': 444.0,
 'ABBOTSFORD ST': 316.0,
 'ABBY RD': 806.0,
 'ABERDEEN ST': 629.0,
 'ACADEMY HILL RD': 771.0,
 'ACADEMY TER': 304.0,
 'ACHORN CIR': 649.0,
 'ACKLEY PL': 574.0,
 'ACORN ST': 70.0,
 'ADAIR RD': 759.0,
 'ADAMS ST': 347.0,
 'ADAMS TER': 364.0,
 'ADANAC TER': 393.0,
 'ADDELAIDE PL': 739.0,
 'ADDINGTON RD': 739.0,
 'ADELAIDE ST': 637.0,
 'ADELLA PL': 795.0,
 'ADRIAN ST': 324.0,
 'AGASSIZ RD': 617.0,
 'AGAWAM ST': 368.0,
 'AGNES AVE': 488.0,
 'AGUADILLA ST': 158.0,
 'AINSLEY ST': 460.0,
 'AIRPORT RD': 36.0,
 'AKRON PL': 294.0,
 'AL ZWIERCAN WAY': 186.0,
 'ALABAMA ST': 470.0,
 'ALAMEDA RD': 692.0,
 'ALARIC ST': 719.0,
 'ALARIC TER': 719.0,
 'ALASKA ST': 265.0,
 'ALBANY ST': 171.0,
 'ALBEMARLE ST': 145.0,
 'ALBERTA ST': 588.0,
 'ALBION PL': 52.0,
 'ALBION ST': 182.0,
 'ALBRIGHT ST': 742.0,
 'ALCOTT ST': 816.0,
 'ALDIE ST': 809.0,
 'ALDO TER': 516.0,
 'ALDRICH ST': 687.0,
 'ALDWIN RD': 564.0,
 'ALDWORTH ST': 644.0,
 'ALEXANDER ST': 259.0,
 'ALFRED ST': 645.0,


In [14]:
mask = df["REPORTING_AREA"].isna()
df.loc[mask, "REPORTING_AREA"] = df.loc[mask, "STREET_CLEAN"].map(street_to_area)
mask = df["REPORTING_AREA"].isna()
df.loc[mask, "REPORTING_AREA"] = df.loc[mask, "STREET_CLEAN"].map(street_to_area)
mask = df["REPORTING_AREA"].isna()
df.loc[mask, "REPORTING_AREA"] = df.loc[mask, "STREET_CLEAN"].map(street_to_area)

In [15]:
df.isnull().sum()
# REPORTING_AREA         9681

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT               1538
REPORTING_AREA         9081
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN           8658
dtype: int64

In [16]:
checks = {
    "STREET present but REPORTING_AREA missing":
        df['STREET'].notna() & df['REPORTING_AREA'].isna(),
}

for name, mask in checks.items():
    print(f"{name}: {mask.sum()}")

STREET present but REPORTING_AREA missing: 1281


In [17]:
latlong_to_area = (
    df.dropna(subset=['LAT_LONG_4F', 'REPORTING_AREA'])
    .groupby(['LAT_LONG_4F'])['REPORTING_AREA']
    .agg(lambda x: x.value_counts().idxmax())
    .to_dict()
)

latlong_to_area

{'(42.2324, -71.1297)': 526.0,
 '(42.2326, -71.1306)': 526.0,
 '(42.2328, -71.13)': 526.0,
 '(42.2329, -71.1316)': 527.0,
 '(42.233, -71.1281)': 527.0,
 '(42.2331, -71.131)': 526.0,
 '(42.2331, -71.1326)': 527.0,
 '(42.2333, -71.132)': 527.0,
 '(42.2333, -71.1336)': 527.0,
 '(42.2334, -71.1386)': 528.0,
 '(42.2335, -71.1291)': 526.0,
 '(42.2335, -71.1345)': 527.0,
 '(42.2336, -71.1329)': 527.0,
 '(42.2337, -71.1312)': 526.0,
 '(42.2337, -71.1334)': 527.0,
 '(42.2338, -71.1301)': 526.0,
 '(42.2339, -71.1322)': 527.0,
 '(42.234, -71.1388)': 528.0,
 '(42.2342, -71.1283)': 526.0,
 '(42.2342, -71.1332)': 527.0,
 '(42.2343, -71.1315)': 527.0,
 '(42.2345, -71.1292)': 526.0,
 '(42.2345, -71.1309)': 526.0,
 '(42.2345, -71.1325)': 527.0,
 '(42.2347, -71.1302)': 526.0,
 '(42.2348, -71.1277)': 526.0,
 '(42.2348, -71.1339)': 527.0,
 '(42.2349, -71.1296)': 526.0,
 '(42.2349, -71.1379)': 528.0,
 '(42.235, -71.1328)': 527.0,
 '(42.2351, -71.1279)': 526.0,
 '(42.2352, -71.1291)': 526.0,
 '(42.2354, -71

In [18]:
mask = df["REPORTING_AREA"].isna()
df.loc[mask, "REPORTING_AREA"] = df.loc[mask, "LAT_LONG_4F"].map(latlong_to_area)
mask = df["REPORTING_AREA"].isna()
df.loc[mask, "REPORTING_AREA"] = df.loc[mask, "LAT_LONG_4F"].map(latlong_to_area)
mask = df["REPORTING_AREA"].isna()
df.loc[mask, "REPORTING_AREA"] = df.loc[mask, "LAT_LONG_4F"].map(latlong_to_area)

In [19]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT               1538
REPORTING_AREA         9079
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN           8658
dtype: int64

# FILLING DISTRCT COLUMN

In [20]:
area_to_district = (
    df.dropna(subset=['REPORTING_AREA', 'DISTRICT'])
    .groupby(['REPORTING_AREA'])['DISTRICT']
    .agg(lambda x: x.value_counts().idxmax())
    .to_dict()
)
area_to_district

{0.0: 'B2',
 1.0: 'A7',
 2.0: 'A7',
 3.0: 'A7',
 4.0: 'A7',
 5.0: 'A7',
 6.0: 'A7',
 7.0: 'A7',
 8.0: 'A7',
 9.0: 'A7',
 10.0: 'A7',
 11.0: 'A7',
 12.0: 'A7',
 13.0: 'A7',
 14.0: 'A7',
 15.0: 'A7',
 16.0: 'A7',
 17.0: 'A7',
 18.0: 'A7',
 19.0: 'A7',
 20.0: 'A7',
 21.0: 'A7',
 22.0: 'A7',
 23.0: 'A7',
 24.0: 'A7',
 25.0: 'A7',
 26.0: 'A7',
 27.0: 'A7',
 28.0: 'A7',
 29.0: 'A7',
 30.0: 'A7',
 31.0: 'A7',
 32.0: 'A7',
 33.0: 'A7',
 34.0: 'A7',
 35.0: 'A7',
 36.0: 'A7',
 37.0: 'A15',
 38.0: 'A15',
 39.0: 'A15',
 40.0: 'A15',
 41.0: 'A15',
 42.0: 'A15',
 43.0: 'A15',
 44.0: 'A15',
 45.0: 'A15',
 46.0: 'A15',
 47.0: 'A15',
 48.0: 'A15',
 49.0: 'A15',
 50.0: 'A15',
 51.0: 'A15',
 52.0: 'A15',
 53.0: 'A15',
 54.0: 'A15',
 55.0: 'A15',
 56.0: 'A15',
 57.0: 'A15',
 58.0: 'A15',
 59.0: 'A15',
 60.0: 'A15',
 61.0: 'A1',
 62.0: 'A1',
 63.0: 'A1',
 64.0: 'A1',
 65.0: 'A1',
 66.0: 'A1',
 67.0: 'A1',
 68.0: 'A1',
 69.0: 'A1',
 70.0: 'A1',
 71.0: 'A1',
 72.0: 'A1',
 73.0: 'A1',
 74.0: 'B3',
 75.0: 'A1'

In [21]:
mask = df["DISTRICT"].isna()
df.loc[mask, "DISTRICT"] = df.loc[mask, "REPORTING_AREA"].map(area_to_district)
mask = df["DISTRICT"].isna()
df.loc[mask, "DISTRICT"] = df.loc[mask, "REPORTING_AREA"].map(area_to_district)
mask = df["DISTRICT"].isna()
df.loc[mask, "DISTRICT"] = df.loc[mask, "REPORTING_AREA"].map(area_to_district)

In [22]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT                656
REPORTING_AREA         9079
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN           8658
dtype: int64

In [23]:
latlong_to_district = (
    df.dropna(subset=['LAT_LONG_4F', 'DISTRICT'])
    .groupby(['LAT_LONG_4F'])['DISTRICT']
    .agg(lambda x: x.value_counts().idxmax())
    .to_dict()
)

latlong_to_district

{'(42.2324, -71.1297)': 'E18',
 '(42.2326, -71.1306)': 'E18',
 '(42.2328, -71.13)': 'E18',
 '(42.2329, -71.1316)': 'E18',
 '(42.233, -71.1281)': 'E18',
 '(42.2331, -71.131)': 'E18',
 '(42.2331, -71.1326)': 'E18',
 '(42.2333, -71.132)': 'E18',
 '(42.2333, -71.1336)': 'E18',
 '(42.2334, -71.1386)': 'E18',
 '(42.2335, -71.1291)': 'E18',
 '(42.2335, -71.1345)': 'E18',
 '(42.2336, -71.1329)': 'E18',
 '(42.2337, -71.1312)': 'E18',
 '(42.2337, -71.1334)': 'E18',
 '(42.2338, -71.1301)': 'E18',
 '(42.2339, -71.1322)': 'E18',
 '(42.234, -71.1388)': 'E18',
 '(42.2342, -71.1283)': 'E18',
 '(42.2342, -71.1332)': 'E18',
 '(42.2343, -71.1315)': 'E18',
 '(42.2345, -71.1292)': 'E18',
 '(42.2345, -71.1309)': 'E18',
 '(42.2345, -71.1325)': 'E18',
 '(42.2347, -71.1302)': 'E18',
 '(42.2348, -71.1277)': 'E18',
 '(42.2348, -71.1339)': 'E18',
 '(42.2349, -71.1296)': 'E18',
 '(42.2349, -71.1379)': 'E18',
 '(42.235, -71.1328)': 'E18',
 '(42.2351, -71.1279)': 'E18',
 '(42.2352, -71.1291)': 'E18',
 '(42.2354, -71

In [24]:
mask = df["DISTRICT"].isna()
df.loc[mask, "DISTRICT"] = df.loc[mask, "LAT_LONG_4F"].map(latlong_to_district)
mask = df["DISTRICT"].isna()
df.loc[mask, "DISTRICT"] = df.loc[mask, "LAT_LONG_4F"].map(latlong_to_district)
mask = df["DISTRICT"].isna()
df.loc[mask, "DISTRICT"] = df.loc[mask, "LAT_LONG_4F"].map(latlong_to_district)

In [25]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT                646
REPORTING_AREA         9079
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN           8658
dtype: int64

# REVERSE FILLING ALL COLUMNS

In [26]:
# now we will fill in reverse
# district->area  (random)
# area->street  (random)
# street->lat long  (max value count)

In [27]:
district_to_area=(
    df.dropna(subset=['DISTRICT','REPORTING_AREA'])
    .groupby('DISTRICT')['REPORTING_AREA']
    .apply(list)
    .to_dict()
)
district_to_area

{'A1': [103.0,
  112.0,
  117.0,
  103.0,
  94.0,
  92.0,
  115.0,
  66.0,
  119.0,
  108.0,
  85.0,
  112.0,
  94.0,
  94.0,
  103.0,
  102.0,
  95.0,
  116.0,
  116.0,
  124.0,
  86.0,
  95.0,
  78.0,
  93.0,
  95.0,
  93.0,
  112.0,
  113.0,
  92.0,
  173.0,
  120.0,
  89.0,
  91.0,
  102.0,
  76.0,
  282.0,
  91.0,
  92.0,
  93.0,
  117.0,
  116.0,
  113.0,
  116.0,
  119.0,
  103.0,
  111.0,
  173.0,
  92.0,
  86.0,
  114.0,
  78.0,
  105.0,
  108.0,
  114.0,
  100.0,
  104.0,
  637.0,
  637.0,
  111.0,
  94.0,
  63.0,
  119.0,
  116.0,
  78.0,
  67.0,
  93.0,
  111.0,
  112.0,
  111.0,
  111.0,
  93.0,
  92.0,
  143.0,
  61.0,
  111.0,
  111.0,
  95.0,
  131.0,
  67.0,
  125.0,
  68.0,
  97.0,
  77.0,
  111.0,
  111.0,
  96.0,
  116.0,
  131.0,
  111.0,
  117.0,
  95.0,
  66.0,
  94.0,
  173.0,
  117.0,
  94.0,
  123.0,
  68.0,
  78.0,
  116.0,
  96.0,
  123.0,
  118.0,
  68.0,
  173.0,
  117.0,
  113.0,
  119.0,
  95.0,
  112.0,
  77.0,
  101.0,
  111.0,
  84.0,
  109.0,
  92.0,

In [28]:
mask=df["REPORTING_AREA"].isna()
df.loc[mask,"REPORTING_AREA"]=df.loc[mask,"DISTRICT"].map(lambda d: np.random.choice(district_to_area.get(d, [np.nan])))

In [29]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT                646
REPORTING_AREA          646
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN           8658
dtype: int64

In [30]:
area_to_street=(
    df.dropna(subset=['REPORTING_AREA','STREET_CLEAN'])
    .groupby('REPORTING_AREA')['STREET_CLEAN']
    .apply(list)
    .to_dict()
)
area_to_street

{0.0: ['HILLSIDE ST',
  'CRESCENT',
  'HILLSIDE ST',
  'CRESCENT',
  'THOMPSONS ISLAND',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'EDGEWATER DR',
  'HILLSIDE ST',
  'NEWMARKET SQ',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'CRESCENT',
  'EAGLE SQ',
  'HILLSIDE ST',
  'SYDNEY ST',
  'CRESCENT',
  'THOMPSONS ISLAND',
  'THOMPSONS ISLAND',
  'DORCHESTER AVE',
  'CRESCENT'],
 1.0: ['EVERETT AVE',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'EVERETT AVE',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'EVERETT AVE',
  'EVERETT AVE',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'BENNINGTON ST',
  'EVERETT AVE',
  'BENNINGTON ST',
  'BENNINGTON ST',


In [31]:
mask=df["STREET_CLEAN"].isna()
df.loc[mask,"STREET_CLEAN"]=df.loc[mask,"REPORTING_AREA"].map(lambda d: np.random.choice(area_to_street.get(d, [np.nan])))

In [32]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT                646
REPORTING_AREA          646
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            9753
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN             18
dtype: int64

In [33]:
street_to_coords = (
    df.dropna(subset=['STREET_CLEAN', 'LAT_LONG_4F'])
      .groupby('STREET_CLEAN')['LAT_LONG_4F']
      .apply(list)
      .to_dict()
)


In [34]:
mask = df['LAT_LONG_4F'].isna()

df.loc[mask, 'LAT_LONG_4F'] = (
    df.loc[mask, 'STREET_CLEAN']
      .map(lambda s: np.random.choice(street_to_coords.get(s, [np.nan])))
)

In [35]:
df.isnull().sum()

INCIDENT_NUMBER           0
OFFENSE_CODE              0
OFFENSE_CODE_GROUP        0
DISTRICT                646
REPORTING_AREA          646
OCCURRED_ON_DATE          0
Lat                   19915
Long                  19915
NAME                      0
STREET                 8658
LAT_LONG              19915
LAT_LONG_6F           19915
LAT_LONG_4F            1157
Lat_4f                19915
Long_4f               19915
STREET_NORM            8658
STREET_CLEAN             18
dtype: int64

In [36]:
checks = {
    "STREET present but LAT_LONG missing":
        df['STREET_CLEAN'].notna() & df['LAT_LONG_4F'].isna(),
}

for name, mask in checks.items():
    print(f"{name}: {mask.sum()}")

STREET present but LAT_LONG missing: 1157


In [37]:
cols = ['DISTRICT', 'REPORTING_AREA', 'STREET_CLEAN','LAT_LONG_4F']

rows_to_drop = df[cols].isna().any(axis=1).sum()
total_rows = len(df)

print("Rows that will be dropped:", rows_to_drop)
print("Percentage dropped:", (rows_to_drop / total_rows) * 100)

# Rows that will be dropped: 9468
# Percentage dropped: 3.0198645079802504

Rows that will be dropped: 1330
Percentage dropped: 0.42433040343292866


In [38]:
cols = ['DISTRICT', 'REPORTING_AREA', 'STREET_CLEAN']

rows_to_drop = df[cols].isna().any(axis=1).sum()
total_rows = len(df)

print("Rows that will be dropped:", rows_to_drop)
print("Percentage dropped:", (rows_to_drop / total_rows) * 100)

Rows that will be dropped: 646
Percentage dropped: 0.20610333881027962


In [39]:
df

INCIDENT_NUMBER  OFFENSE_CODE            OFFENSE_CODE_GROUP DISTRICT  \
0           I182070945           619                       Larceny      D14   
1           I182070885           619                       Larceny       B3   
2           I182070816           619                       Larceny       C6   
3           I182070777           619                       Larceny      C11   
4           I182070707           619                       Larceny      D14   
...                ...           ...                           ...      ...   
313430   I130126035-00           338                       Robbery      C11   
313431   I130041200-00           547  Burglary - No Property Taken       B3   
313432   I120720047-00           334                       Robbery      E13   
313433   I120719309-00           530           Commercial Burglary       A1   
313434   I060168073-00          1864                Drug Violation      E13   

        REPORTING_AREA  OCCURRED_ON_DATE        Lat       Long  \
0                808.0  02-09-2018 13:00  42.357791 -71.139371   
1                456.0  03-09-2018 17:17  42.301546 -71.081182   
2                185.0  03-09-2018 12:45  42.321987 -71.062807   
3                388.0  23-08-2018 13:34  42.272306 -71.067214   
4                782.0  02-09-2018 23:12  42.352935 -71.140501   
...                ...               ...        ...        ...   
313430           252.0  09-02-2016 13:55        NaN        NaN   
313431           428.0  07-12-2015 11:38  42.314334 -71.097914   
313432           565.0  17-07-2015 09:23        NaN        NaN   
313433           119.0  27-07-2015 12:00  42.352418 -71.065255   
313434           912.0  27-01-2018 14:01  42.322838 -71.100967   

                                               NAME             STREET  \
0                         LARCENY OTHER $200 & OVER         LINCOLN ST   
1                         LARCENY OTHER $200 & OVER       ELLINGTON ST   
2                         LARCENY OTHER $200 & OVER  MASSACHUSETTS AVE   
3                         LARCENY OTHER $200 & OVER           ADAMS ST   
4                         LARCENY OTHER $200 & OVER          GORDON ST   
...                                             ...                ...   
313430                ROBBERY - UNARMED - RESIDENCE     SAVIN HILL AVE   
313431        B&E NON-RESIDENCE DAY - NO PROP TAKEN         DIXWELL ST   
313432                 ROBBERY - UNARMED - BUSINESS                NaN   
313433              B&E NON-RESIDENCE NIGHT - FORCE        BOYLSTON ST   
313434  DRUGS - POSS CLASS D - INTENT MFR DIST DISP          CENTRE ST   

                           LAT_LONG              LAT_LONG_6F  \
0       (42.35779134, -71.13937053)   (42.357791, -71.13937)   
1       (42.30154555, -71.08118184)  (42.301545, -71.081181)   
2       (42.32198656, -71.06280666)  (42.321986, -71.062806)   
3       (42.27230624, -71.06721386)  (42.272306, -71.067213)   
4       (42.35293536, -71.14050052)    (42.352935, -71.1405)   
...                             ...                      ...   
313430                          NaN                      NaN   
313431  (42.31433402, -71.09791405)  (42.314334, -71.097914)   
313432                          NaN                      NaN   
313433  (42.35241815, -71.06525499)  (42.352418, -71.065254)   
313434  (42.32283759, -71.10096723)  (42.322837, -71.100967)   

                LAT_LONG_4F   Lat_4f  Long_4f        STREET_NORM  \
0       (42.3577, -71.1393)  42.3577 -71.1393         LINCOLN ST   
1       (42.3015, -71.0811)  42.3015 -71.0811       ELLINGTON ST   
2       (42.3219, -71.0628)  42.3219 -71.0628  MASSACHUSETTS AVE   
3       (42.2723, -71.0672)  42.2723 -71.0672           ADAMS ST   
4       (42.3529, -71.1405)  42.3529 -71.1405          GORDON ST   
...                     ...      ...      ...                ...   
313430  (42.3129, -71.0566)      NaN      NaN     SAVIN HILL AVE   
313431  (42.3143, -71.0979)  42.3143 -71.0979         DIXWELL S

In [40]:
# DISTRICT                255
# REPORTING_AREA         8502
# Lat                   19278 DROP
# Long                  19278 DROP
# STREET                 8616 DROP
# LAT_LONG              19278 DROP
# LAT_LONG_6F           19278 DROP
# LAT_LONG_4F            9138 SPLIT INTO LAT & LONG IN FLOAT DATATYPE
# Lat_4f                19278 DROP
# Long_4f               19278 DROP
# STREET_NORM            8616 DROP
# STREET_CLEAN           8616 RENAME TO STREET

In [41]:
# ---------- DROP ----------
cols_to_drop = [
    'Lat', 'Long', 'LAT_LONG',
    'LAT_LONG_6F', 'Lat_4f', 'Long_4f',
    'STREET_NORM', 'STREET'
]
df = df.drop(columns=cols_to_drop)

# ---------- SPLIT ----------
df[['LAT', 'LONG']] = (
    df['LAT_LONG_4F']
    .str.replace('[()]', '', regex=True)
    .str.split(',', expand=True)
)

df['LAT'] = df['LAT'].astype(float)
df['LONG'] = df['LONG'].astype(float)

# ---------- RENAME ----------
df = df.rename(columns={
    'STREET_CLEAN': 'STREET'
})


In [42]:
df

INCIDENT_NUMBER  OFFENSE_CODE            OFFENSE_CODE_GROUP DISTRICT  \
0           I182070945           619                       Larceny      D14   
1           I182070885           619                       Larceny       B3   
2           I182070816           619                       Larceny       C6   
3           I182070777           619                       Larceny      C11   
4           I182070707           619                       Larceny      D14   
...                ...           ...                           ...      ...   
313430   I130126035-00           338                       Robbery      C11   
313431   I130041200-00           547  Burglary - No Property Taken       B3   
313432   I120720047-00           334                       Robbery      E13   
313433   I120719309-00           530           Commercial Burglary       A1   
313434   I060168073-00          1864                Drug Violation      E13   

        REPORTING_AREA  OCCURRED_ON_DATE  \
0                808.0  02-09-2018 13:00   
1                456.0  03-09-2018 17:17   
2                185.0  03-09-2018 12:45   
3                388.0  23-08-2018 13:34   
4                782.0  02-09-2018 23:12   
...                ...               ...   
313430           252.0  09-02-2016 13:55   
313431           428.0  07-12-2015 11:38   
313432           565.0  17-07-2015 09:23   
313433           119.0  27-07-2015 12:00   
313434           912.0  27-01-2018 14:01   

                                               NAME          LAT_LONG_4F  \
0                         LARCENY OTHER $200 & OVER  (42.3577, -71.1393)   
1                         LARCENY OTHER $200 & OVER  (42.3015, -71.0811)   
2                         LARCENY OTHER $200 & OVER  (42.3219, -71.0628)   
3                         LARCENY OTHER $200 & OVER  (42.2723, -71.0672)   
4                         LARCENY OTHER $200 & OVER  (42.3529, -71.1405)   
...                                             ...                  ...   
313430                ROBBERY - UNARMED - RESIDENCE  (42.3129, -71.0566)   
313431        B&E NON-RESIDENCE DAY - NO PROP TAKEN  (42.3143, -71.0979)   
313432                 ROBBERY - UNARMED - BUSINESS   (42.292, -71.0939)   
313433              B&E NON-RESIDENCE NIGHT - FORCE  (42.3524, -71.0652)   
313434  DRUGS - POSS CLASS D - INTENT MFR DIST DISP  (42.3228, -71.1009)   

                   STREET      LAT     LONG  
0              LINCOLN ST  42.3577 -71.1393  
1            ELLINGTON ST  42.3015 -71.0811  
2       MASSACHUSETTS AVE  42.3219 -71.0628  
3                ADAMS ST  42.2723 -71.0672  
4               GORDON ST  42.3529 -71.1405  
...                   ...      ...      ...  
313430     SAVIN HILL AVE  42.3129 -71.0566  
313431         DIXWELL ST  42.3143 -71.0979  
313432         OSPREY WAY  42.2920 -71.0939  
313433        BOYLSTON ST  42.3524 -71.0652  
313434          CENTRE ST  42.3228 -71.1009  

[313435 rows x 11 columns]

In [43]:
df[['DATE', 'TIME']] = df['OCCURRED_ON_DATE'].str.split(' ', expand=True)
df = df.drop(columns=['OCCURRED_ON_DATE'])


In [44]:
df

INCIDENT_NUMBER  OFFENSE_CODE            OFFENSE_CODE_GROUP DISTRICT  \
0           I182070945           619                       Larceny      D14   
1           I182070885           619                       Larceny       B3   
2           I182070816           619                       Larceny       C6   
3           I182070777           619                       Larceny      C11   
4           I182070707           619                       Larceny      D14   
...                ...           ...                           ...      ...   
313430   I130126035-00           338                       Robbery      C11   
313431   I130041200-00           547  Burglary - No Property Taken       B3   
313432   I120720047-00           334                       Robbery      E13   
313433   I120719309-00           530           Commercial Burglary       A1   
313434   I060168073-00          1864                Drug Violation      E13   

        REPORTING_AREA                                         NAME  \
0                808.0                    LARCENY OTHER $200 & OVER   
1                456.0                    LARCENY OTHER $200 & OVER   
2                185.0                    LARCENY OTHER $200 & OVER   
3                388.0                    LARCENY OTHER $200 & OVER   
4                782.0                    LARCENY OTHER $200 & OVER   
...                ...                                          ...   
313430           252.0                ROBBERY - UNARMED - RESIDENCE   
313431           428.0        B&E NON-RESIDENCE DAY - NO PROP TAKEN   
313432           565.0                 ROBBERY - UNARMED - BUSINESS   
313433           119.0              B&E NON-RESIDENCE NIGHT - FORCE   
313434           912.0  DRUGS - POSS CLASS D - INTENT MFR DIST DISP   

                LAT_LONG_4F             STREET      LAT     LONG        DATE  \
0       (42.3577, -71.1393)         LINCOLN ST  42.3577 -71.1393  02-09-2018   
1       (42.3015, -71.0811)       ELLINGTON ST  42.3015 -71.0811  03-09-2018   
2       (42.3219, -71.0628)  MASSACHUSETTS AVE  42.3219 -71.0628  03-09-2018   
3       (42.2723, -71.0672)           ADAMS ST  42.2723 -71.0672  23-08-2018   
4       (42.3529, -71.1405)          GORDON ST  42.3529 -71.1405  02-09-2018   
...                     ...                ...      ...      ...         ...   
313430  (42.3129, -71.0566)     SAVIN HILL AVE  42.3129 -71.0566  09-02-2016   
313431  (42.3143, -71.0979)         DIXWELL ST  42.3143 -71.0979  07-12-2015   
313432   (42.292, -71.0939)         OSPREY WAY  42.2920 -71.0939  17-07-2015   
313433  (42.3524, -71.0652)        BOYLSTON ST  42.3524 -71.0652  27-07-2015   
313434  (42.3228, -71.1009)          CENTRE ST  42.3228 -71.1009  27-01-2018   

         TIME  
0       13:00  
1       17:17  
2       12:45  
3       13:34  
4       23:12  
...       ...  
313430  13:55  
313431  11:38  
313432  09:23  
313433  12:00  
313434  14:01  

[313435 rows x 12 columns]

In [45]:
df = df[
    ['INCIDENT_NUMBER',
     'OFFENSE_CODE',
     'OFFENSE_CODE_GROUP',
     'DISTRICT',
     'REPORTING_AREA',
     'STREET',
     'LAT_LONG_4F',
     'LAT',
     'LONG',
     'DATE',
     'TIME',
     'NAME']
]

In [46]:
df

INCIDENT_NUMBER  OFFENSE_CODE            OFFENSE_CODE_GROUP DISTRICT  \
0           I182070945           619                       Larceny      D14   
1           I182070885           619                       Larceny       B3   
2           I182070816           619                       Larceny       C6   
3           I182070777           619                       Larceny      C11   
4           I182070707           619                       Larceny      D14   
...                ...           ...                           ...      ...   
313430   I130126035-00           338                       Robbery      C11   
313431   I130041200-00           547  Burglary - No Property Taken       B3   
313432   I120720047-00           334                       Robbery      E13   
313433   I120719309-00           530           Commercial Burglary       A1   
313434   I060168073-00          1864                Drug Violation      E13   

        REPORTING_AREA             STREET          LAT_LONG_4F      LAT  \
0                808.0         LINCOLN ST  (42.3577, -71.1393)  42.3577   
1                456.0       ELLINGTON ST  (42.3015, -71.0811)  42.3015   
2                185.0  MASSACHUSETTS AVE  (42.3219, -71.0628)  42.3219   
3                388.0           ADAMS ST  (42.2723, -71.0672)  42.2723   
4                782.0          GORDON ST  (42.3529, -71.1405)  42.3529   
...                ...                ...                  ...      ...   
313430           252.0     SAVIN HILL AVE  (42.3129, -71.0566)  42.3129   
313431           428.0         DIXWELL ST  (42.3143, -71.0979)  42.3143   
313432           565.0         OSPREY WAY   (42.292, -71.0939)  42.2920   
313433           119.0        BOYLSTON ST  (42.3524, -71.0652)  42.3524   
313434           912.0          CENTRE ST  (42.3228, -71.1009)  42.3228   

           LONG        DATE   TIME  \
0      -71.1393  02-09-2018  13:00   
1      -71.0811  03-09-2018  17:17   
2      -71.0628  03-09-2018  12:45   
3      -71.0672  23-08-2018  13:34   
4      -71.1405  02-09-2018  23:12   
...         ...         ...    ...   
313430 -71.0566  09-02-2016  13:55   
313431 -71.0979  07-12-2015  11:38   
313432 -71.0939  17-07-2015  09:23   
313433 -71.0652  27-07-2015  12:00   
313434 -71.1009  27-01-2018  14:01   

                                               NAME  
0                         LARCENY OTHER $200 & OVER  
1                         LARCENY OTHER $200 & OVER  
2                         LARCENY OTHER $200 & OVER  
3                         LARCENY OTHER $200 & OVER  
4                         LARCENY OTHER $200 & OVER  
...                                             ...  
313430                ROBBERY - UNARMED - RESIDENCE  
313431        B&E NON-RESIDENCE DAY - NO PROP TAKEN  
313432                 ROBBERY - UNARMED - BUSINESS  
313433              B&E NON-RESIDENCE NIGHT - FORCE  
313434  DRUGS - POSS CLASS D - INTENT MFR DIST DISP  

[313435 rows x 12 columns]

In [47]:
df['DATE'] = pd.to_datetime(df['DATE'], dayfirst=True)
df['TIME'] = pd.to_datetime(df['TIME']).dt.time


C:\Users\Nikhil Rawat\AppData\Local\Temp\ipykernel_4840\1127808205.py:2: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['TIME'] = pd.to_datetime(df['TIME']).dt.time


In [48]:
df_coords = df.dropna(
    subset=['DISTRICT', 'REPORTING_AREA', 'STREET', 'LAT', 'LONG']
)

df_coords.to_csv('Cleaned_Crime_Coords.csv', index=False)


In [49]:
df_no_coords = df.drop(columns=['LAT', 'LONG', 'LAT_LONG_4F'])

df_no_coords = df_no_coords.dropna(
    subset=['DISTRICT', 'REPORTING_AREA', 'STREET']
)

df_no_coords.to_csv('Cleaned_Crime.csv', index=False)


In [50]:
df

INCIDENT_NUMBER  OFFENSE_CODE            OFFENSE_CODE_GROUP DISTRICT  \
0           I182070945           619                       Larceny      D14   
1           I182070885           619                       Larceny       B3   
2           I182070816           619                       Larceny       C6   
3           I182070777           619                       Larceny      C11   
4           I182070707           619                       Larceny      D14   
...                ...           ...                           ...      ...   
313430   I130126035-00           338                       Robbery      C11   
313431   I130041200-00           547  Burglary - No Property Taken       B3   
313432   I120720047-00           334                       Robbery      E13   
313433   I120719309-00           530           Commercial Burglary       A1   
313434   I060168073-00          1864                Drug Violation      E13   

        REPORTING_AREA             STREET          LAT_LONG_4F      LAT  \
0                808.0         LINCOLN ST  (42.3577, -71.1393)  42.3577   
1                456.0       ELLINGTON ST  (42.3015, -71.0811)  42.3015   
2                185.0  MASSACHUSETTS AVE  (42.3219, -71.0628)  42.3219   
3                388.0           ADAMS ST  (42.2723, -71.0672)  42.2723   
4                782.0          GORDON ST  (42.3529, -71.1405)  42.3529   
...                ...                ...                  ...      ...   
313430           252.0     SAVIN HILL AVE  (42.3129, -71.0566)  42.3129   
313431           428.0         DIXWELL ST  (42.3143, -71.0979)  42.3143   
313432           565.0         OSPREY WAY   (42.292, -71.0939)  42.2920   
313433           119.0        BOYLSTON ST  (42.3524, -71.0652)  42.3524   
313434           912.0          CENTRE ST  (42.3228, -71.1009)  42.3228   

           LONG       DATE      TIME  \
0      -71.1393 2018-09-02  13:00:00   
1      -71.0811 2018-09-03  17:17:00   
2      -71.0628 2018-09-03  12:45:00   
3      -71.0672 2018-08-23  13:34:00   
4      -71.1405 2018-09-02  23:12:00   
...         ...        ...       ...   
313430 -71.0566 2016-02-09  13:55:00   
313431 -71.0979 2015-12-07  11:38:00   
313432 -71.0939 2015-07-17  09:23:00   
313433 -71.0652 2015-07-27  12:00:00   
313434 -71.1009 2018-01-27  14:01:00   

                                               NAME  
0                         LARCENY OTHER $200 & OVER  
1                         LARCENY OTHER $200 & OVER  
2                         LARCENY OTHER $200 & OVER  
3                         LARCENY OTHER $200 & OVER  
4                         LARCENY OTHER $200 & OVER  
...                                             ...  
313430                ROBBERY - UNARMED - RESIDENCE  
313431        B&E NON-RESIDENCE DAY - NO PROP TAKEN  
313432                 ROBBERY - UNARMED - BUSINESS  
313433              B&E NON-RESIDENCE NIGHT - FORCE  
313434  DRUGS - POSS CLASS D - INTENT MFR DIST DISP  

[313435 rows x 12 columns]